### A cluster has been created for this demo
To run this demo, just select the cluster `dbdemos-llm-rag-chatbot-ling_huang` from the dropdown menu ([open cluster configuration](https://dbc-57a6b8b4-32b6.cloud.databricks.com/#setting/clusters/1212-021800-o0bqrfse/configuration)). <br />
*Note: If the cluster was deleted after 30 days, you can re-create it with `dbdemos.create_cluster('llm-rag-chatbot')` or re-install the demo: `dbdemos.install('llm-rag-chatbot')`*


# 1/ Data preparation for LLM Chatbot RAG

## Building and indexing our knowledge base into Databricks Vector Search

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-flow-1.png?raw=true" style="float: right; width: 800px; margin-left: 10px">

In this notebook, we'll ingest our documentation pages and index them with a Vector Search index to help our chatbot provide better answers.

Preparing high quality data is key for your chatbot performance. We recommend taking time to implement these next steps with your own dataset.

Thankfully, Lakehouse AI provides state of the art solutions to accelerate your AI and LLM projects, and also simplifies data ingestion and preparation at scale.

For this example, we will use Databricks documentation from [docs.databricks.com](docs.databricks.com):
- Download the web pages
- Split the pages in small chunks of text
- Compute the embeddings using a Databricks Foundation model as part of our Delta Table
- Create a Vector Search index based on our Delta Table  

<!-- Collect usage data (view). Remove it to disable collection or disable tracker during installation. View README for more details.  -->
<img width="1px" src="https://ppxrzfxige.execute-api.us-west-2.amazonaws.com/v1/analytics?category=data-science&org_id=local&notebook=%2F01-Data-Preparation-and-Index&demo_name=llm-rag-chatbot&event=VIEW&path=%2F_dbdemos%2Fdata-science%2Fllm-rag-chatbot%2F01-Data-Preparation-and-Index&version=1">

In [0]:
%pip install "git+https://github.com/mlflow/mlflow.git@gateway-migration" lxml==4.9.3 transformers==4.30.2 langchain==0.0.344 databricks-vectorsearch==0.22
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Cloning https://github.com/mlflow/mlflow.git (to revision gateway-migration) to /tmp/pip-req-build-5yylyl1p
  Running command git clone --filter=blob:none --quiet https://github.com/mlflow/mlflow.git /tmp/pip-req-build-5yylyl1p
  Running command git checkout -b gateway-migration --track origin/gateway-migration
  Switched to a new branch 'gateway-migration'
  branch 'gateway-migration' set up to track 'origin/gateway-migration'.
  Resolved https://github.com/mlflow/mlflow.git to commit db1e9e851f873aefe2bdc4938a316d665e67fed2
  Running command git submodule update --init --recursive -q
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml):

In [0]:
%run ./_resources/00-init $reset_all_data=false

using catalog.database `ling_test_demo`.`default`


DataFrame[]

## Extracting Databricks documentation sitemap and pages

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-1.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

First, let's create our raw dataset as a Delta Lake table.

For this demo, we will directly download a few documentation pages from `docs.databricks.com` and save the HTML content.

Here are the main steps:

- Run a quick script to extract the page URLs from the `sitemap.xml` file
- Download the web pages
- Use BeautifulSoup to extract the ArticleBody
- Save the HTML results in a Delta Lake table

In [0]:
if not spark.catalog.tableExists("raw_documentation") or spark.table("raw_documentation").isEmpty():
    # Download Databricks documentation to a DataFrame (see _resources/00-init for more details)
    doc_articles = download_databricks_documentation_articles()
    #Save them as a raw_documentation table
    doc_articles.write.mode('overwrite').saveAsTable("raw_documentation")

display(spark.table("raw_documentation").limit(2))

url text https://docs.databricks.com/en/data-sharing/access-list.html 
 
 Use IP access lists to restrict Delta Sharing recipient access (open sharing) 
 This article describes how data providers can assign IP access lists to control recipient access to shared data. 
 If you, as a data provider, are using the open Delta Sharing protocol , you can limit a recipient to a restricted set of IP addresses when they access data that you share. This list is independent of Workspace IP access lists . Only allow lists are supported. 
 The IP access list affects the following: 
 
 Delta Sharing OSS Protocol REST API access 
 Delta Sharing activation URL access 
 Delta Sharing credential file download 
 
 Each recipient supports a maximum of 100 IP/CIDR values, where one CIDR counts as a single value. Only IPv4 addresses are supported. 
 
 Assign an IP access list to a recipient 
 You can assign an IP access list to a recipient using Catalog Explorer or the Databricks Unity Catalog CLI. 
 Permissions required : If you are assigning an IP access list when you create a recipient, you must be a metastore admin or user with the CREATE_RECIPIENT privilege. If you are assigning an IP access list to an existing recipient, you must be the recipient object owner. 
 
 
 
 In your Databricks workspace, click Catalog . 
 In the left pane, expand the Delta Sharing menu and select Shared by me . 
 On the Recipients tab, select the recipient. 
 On the IP access list tab, click Add IP address/CIDRs for each IP address (in single IP address format, like 8.8.8.8) or range of IP addresses (in CIDR format, like 8.8.8.4/10). 
 
 
 
 To add an IP access list when you create a new recipient, run the following command using the Databricks CLI , replacing <recipient-name> and the IP address values. 
 databricks unity-catalog recipients create \ 
 --name <recipient-name> \ 
 --allowed-ip-address = 8 .8.8.8 \ 
 --allowed-ip-address = 8 .8.8.4/10
 
 
 To add an IP access list to an existing recipient, run the following command, replacing <recipient-name> and the IP address values. 
 databricks unity-catalog recipients update \ 
 --name <recipient-name> \ 
 --json = '{"ip_access_list": {"allowed_ip_addresses": ["8.8.8.8", "8.8.8.4/10"]}}' 
 
 
 
 
 
 
 Remove an IP access list 
 You can remove a recipient’s IP access list using Catalog Explorer or the Databricks Unity Catalog CLI. If you remove all IP addresses from the list, the recipient can access the shared data from anywhere. 
 Permissions required : Recipient object owner. 
 
 
 
 In your Databricks workspace, click Catalog . 
 In the left pane, expand the Delta Sharing menu and select Shared by me . 
 On the Recipients tab, select the recipient. 
 On the IP access list tab, click the trash can icon next to the IP address you want to delete. 
 
 
 
 Use the Databricks CLI to pass in an empty IP access list: 
 databricks unity-catalog recipients update \ 
 --name <recipient-name> \ 
 --json = '{"ip_access_list": {}}' 
 
 
 
 
 
 
 View a recipient’s IP access list 
 You can view a recipient’s IP access list using Catalog Explorer, the Databricks Unity Catalog CLI, or the DESCRIBE RECIPIENT SQL command in a notebook or Databricks SQL query. 
 Permissions required : Metastore admin, user with the USE RECIPIENT privilege, or the recipient object owner. 
 
 
 
 In your Databricks workspace, click Catalog . 
 In the left pane, expand the Delta Sharing menu and select Shared by me . 
 On the Recipients tab, find and select the recipient. 
 View allowed IP addresses on the IP access list tab. 
 
 
 
 Run the following command using the Databricks CLI . 
 databricks unity-catalog recipients get --name <recipient-name>
 
 
 
 
 Run the following command in a notebook or the Databricks SQL query editor. 
 DESCRIBE RECIPIENT < recipient - name > ; 
 
 
 
 
 
 
 Audit logging for Delta Sharing IP access lists 
 The following operations trigger audit logs related to IP access lists: 
 
 Recipient management operations: creat


### Splitting documentation pages into small chunks

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-2.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

LLM models typically have a maximum input context length, and you won't be able to compute embeddings for very long texts.
In addition, the longer your context length is, the longer it will take for the model to provide a response.

Document preparation is key for your model to perform well, and multiple strategies exist depending on your dataset:

- Split document into small chunks (paragraph, h2...)
- Truncate documents to a fixed length
- The chunk size depends on your content and how you'll be using it to craft your prompt. Adding multiple small doc chunks in your prompt might give different results than sending only a big one
- Split into big chunks and ask a model to summarize each chunk as a one-off job, for faster live inference
- Create multiple agents to evaluate each bigger document in parallel, and ask a final agent to craft your answer...


### Splitting our big documentation pages in smaller chunks (h2 sections)

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/chunk-window-size.png?raw=true" style="float: right" width="700px">
<br/>
In this demo, we have big documentation articles, which are too long for the prompt to our model. 

We won't be able to use multiple documents as RAG context as they would exceed our max input size. Some recent studies also suggest that bigger window size isn't always better, as the LLMs seem to focus on the beginning and end of your prompt.

In our case, we'll split these articles between HTML `h2` tags, remove HTML and ensure that each chunk is less than 500 tokens using LangChain. 

#### LLM Window size and Tokenizer

The same sentence might return different tokens for different models. LLMs are shipped with a `Tokenizer` that you can use to count tokens for a given sentence (usually more than the number of words) (see [Hugging Face documentation](https://huggingface.co/docs/transformers/main/tokenizer_summary) or [OpenAI](https://github.com/openai/tiktoken))

Make sure the tokenizer you'll be using here matches your model. We'll be using the `transformers` library to count llama2 tokens with its tokenizer. This will also keep our document token size below our embedding max size (1024).

<br/>
<br style="clear: both">
<div style="background-color: #def2ff; padding: 15px;  border-radius: 30px; ">
  <strong>Information</strong><br/>
  Remember that the following steps are specific to your dataset. This is a critical part to building a successful RAG assistant.
  <br/> Always take time to manually review the chunks created and ensure that they make sense and contain relevant information.
</div>

In [0]:
from langchain.text_splitter import HTMLHeaderTextSplitter, RecursiveCharacterTextSplitter
from transformers import AutoTokenizer

max_chunk_size = 500

tokenizer = AutoTokenizer.from_pretrained("hf-internal-testing/llama-tokenizer")
text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(tokenizer, chunk_size=max_chunk_size, chunk_overlap=50)
html_splitter = HTMLHeaderTextSplitter(headers_to_split_on=[("h2", "header2")])

# Split on H2, but merge small h2 chunks together to avoid too small. 
def split_html_on_h2(html, min_chunk_size = 20, max_chunk_size=500):
  h2_chunks = html_splitter.split_text(html)
  chunks = []
  previous_chunk = ""
  # Merge chunks together to add text before h2 and avoid too small docs.
  for c in h2_chunks:
    # Concat the h2 (note: we could remove the previous chunk to avoid duplicate h2)
    content = c.metadata.get('header2', "") + "\n" + c.page_content
    if len(tokenizer.encode(previous_chunk + content)) <= max_chunk_size/2:
        previous_chunk += content + "\n"
    else:
        chunks.extend(text_splitter.split_text(previous_chunk.strip()))
        previous_chunk = content + "\n"
  if previous_chunk:
      chunks.extend(text_splitter.split_text(previous_chunk.strip()))
  # Discard too small chunks
  return [c for c in chunks if len(tokenizer.encode(c)) > min_chunk_size]

# Let's create a user-defined function (UDF) to chunk all our documents with spark
@pandas_udf("array<string>")
def parse_and_split(docs: pd.Series) -> pd.Series:
    return docs.apply(split_html_on_h2)
  
# Let's try our chunking function
html = spark.table("raw_documentation").limit(1).collect()[0]['text']
split_html_on_h2(html)

2023-12-24 20:07:07.368957: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-24 20:07:08.648990: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-24 20:07:08.649038: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-24 20:07:08.656385: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-24 20:07:09.203010: I tensorflow/core/platform/cpu_feature_g

['Use IP access lists to restrict Delta Sharing recipient access (open sharing)  \nThis article describes how data providers can assign IP access lists to control recipient access to shared data.  \nIf you, as a data provider, are using the open Delta Sharing protocol, you can limit a recipient to a restricted set of IP addresses when they access data that you share. This list is independent of Workspace IP access lists. Only allow lists are supported.  \nThe IP access list affects the following:  \nDelta Sharing OSS Protocol REST API access  \nDelta Sharing activation URL access  \nDelta Sharing credential file download  \nEach recipient supports a maximum of 100 IP/CIDR values, where one CIDR counts as a single value. Only IPv4 addresses are supported.  \nAssign an IP access list to a recipient',
 'Assign an IP access list to a recipient\nYou can assign an IP access list to a recipient using Catalog Explorer or the Databricks Unity Catalog CLI.  \nPermissions required: If you are ass

## What's required for our Vector Search Index

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/databricks-vector-search-type.png?raw=true" style="float: right" width="800px">

Databricks provides multiple types of vector search indexes:

- **Managed embeddings**: you provide a text column and endpoint name and Databricks synchronizes the index with your Delta table 
- **Self Managed embeddings**: you compute the embeddings and save them as a field of your Delta Table, Databricks will then synchronize the index
- **Direct index**: when you want to use and update the index without having a Delta Table

In this demo, we will show you how to setup a **Self-managed Embeddings** index. 

To do so, we will have to first compute the embeddings of our chunks and save them as a Delta Lake table field as `array&ltfloat&gt`

## Introducing Databricks BGE Embeddings Foundation Model endpoints

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-4.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

Foundation Models are provided by Databricks, and can be used out-of-the-box.

Databricks supports several endpoint types to compute embeddings or evaluate a model:
- A **foundation model endpoint**, provided by Databricks (ex: llama2-70B, MPT...)
- An **external endpoint**, acting as a gateway to an external model (ex: Azure OpenAI)
- A **custom**, fined-tuned model hosted on Databricks model service

Open the [Model Serving Endpoint page](/ml/endpoints) to explore and try the foundation models.

For this demo, we will use the foundation model `BGE` (embeddings) and `llama2-70B` (chat). <br/><br/>

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/databricks-foundation-models.png?raw=true" width="600px" >

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": ["What is Apache Spark?"]})
embeddings = [e['embedding'] for e in response.data]
print(embeddings)
# NOTE: if you change your embedding model here, make sure you change it in the query step too

[[0.0186004638671875, -0.0141448974609375, -0.0574951171875, 0.0034027099609375, 0.008453369140625, -0.0216064453125, -0.02471923828125, -0.004688262939453125, 0.0136566162109375, 0.050384521484375, -0.0272064208984375, -0.01470184326171875, 0.054718017578125, -0.0538330078125, -0.01035308837890625, -0.0162200927734375, -0.0188140869140625, -0.017242431640625, -0.051300048828125, 0.0177764892578125, 0.00434112548828125, 0.0284423828125, -0.055633544921875, -0.037689208984375, -0.001373291015625, 0.0203704833984375, -0.046661376953125, 0.01580810546875, 0.0938720703125, 0.0195770263671875, -0.044647216796875, -0.0124359130859375, -0.0062255859375, -0.0293121337890625, 0.04327392578125, -0.02557373046875, 0.049468994140625, 0.03228759765625, -0.06011962890625, -0.0126495361328125, 0.0218658447265625, -0.0099945068359375, 0.0135650634765625, -0.04058837890625, -0.0777587890625, -0.040863037109375, 0.003063201904296875, -0.03369140625, -0.01284027099609375, -0.040985107421875, -0.039794921

In [0]:
%sql
--Note that we need to enable Change Data Feed on the table to create the index
CREATE TABLE IF NOT EXISTS databricks_documentation (
  id BIGINT GENERATED BY DEFAULT AS IDENTITY,
  url STRING,
  content STRING,
  embedding ARRAY <FLOAT>
) TBLPROPERTIES (delta.enableChangeDataFeed = true); 

### Computing the chunk embeddings and saving them to our Delta Table

The last step is to compute an embedding for all our documentation chunks. Let's create a udf to compute the embeddings using the foundation model endpoint.

*Note that this part would typically be setup as a production-grade job, running as soon as a new documentation page is updated. <br/> This could be setup as a Delta Live Table pipeline to incrementally consume updates.*

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

@pandas_udf("array<float>")
def get_embedding(contents: pd.Series) -> pd.Series:
    def get_embeddings(batch):
        #Note: this will gracefully fail if an exception is thrown during embedding creation (add try/except if needed) 
        response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": batch})
        return [e['embedding'] for e in response.data]

    # Splitting the contents into batches of 150 items each, since the embedding model takes at most 150 inputs per request.
    max_batch_size = 150
    batches = [contents.iloc[i:i + max_batch_size] for i in range(0, len(contents), max_batch_size)]

    # Process each batch and collect the results
    all_embeddings = []
    for batch in batches:
        all_embeddings += get_embeddings(batch.tolist())

    return pd.Series(all_embeddings)

In [0]:
(spark.table("raw_documentation")
      .withColumn('content', F.explode(parse_and_split('text')))
      .withColumn('embedding', get_embedding('content'))
      .drop("text")
      .write.mode('overwrite').saveAsTable("databricks_documentation"))

display(spark.table("databricks_documentation"))

id url content embedding 8658 https://docs.databricks.com/en/delegated-auth.html Delegated authentication to third-party services 
Databricks can log you into third-party services, such as the Ideas Portal (powered by Aha!) and the Help Center (powered by Salesforce), using your Databricks username. These third-party services delegate authentication to Databricks, essentially putting Databricks in the role of single sign-on (SSO) provider. 
For example, with delegated authentication enabled, when you go to the help menu in your Databricks workspace and select Feedback, you’ll be logged into the Ideas Portal immediately, without having to provide credentials again. 
Note 
Delegated authentication is enabled by default for all Databricks accounts, but your administrator may choose to disable it. 
This article describes how each of the third-party services that delegate authentication to Databricks works. 
Ideas Portal List(-0.0031833649, -0.031982422, -0.034118652, -0.0043411255, -0.01953125, 0.0016212463, -0.00995636, 0.0073432922, -0.037902832, 0.027633667, -0.025146484, 0.016540527, 0.058654785, -0.043792725, -0.030883789, 0.028625488, 0.0052948, 0.023788452, -0.040740967, 0.014572144, 0.044708252, 0.029403687, -0.04699707, -0.0022850037, -0.037628174, 0.04067993, -0.003921509, -2.2256374E-4, 0.09069824, 0.012718201, -0.01626587, -0.027740479, 0.034454346, -0.028213501, -0.020935059, 0.0078086853, 0.010314941, -0.053497314, -0.041290283, -0.01776123, 0.009284973, 0.06915283, 0.015213013, -0.035461426, -0.036376953, 0.016311646, -0.04711914, -0.018569946, -0.024169922, -0.040130615, -0.055847168, 0.013977051, 0.008422852, -0.004627228, -0.01272583, -0.058654785, -0.021850586, 0.027511597, -0.041809082, 0.007080078, 0.034057617, 0.033325195, -0.022628784, -0.06121826, 0.053771973, 0.032958984, -0.0055160522, -0.0016889572, -0.03390503, -0.025634766, -0.012481689, 0.05038452, 0.0028018951, -0.03741455, -0.032104492, 0.0049362183, 0.0053634644, 0.008544922, -7.133484E-4, 0.03552246, 0.006248474, 0.013748169, 0.0035934448, -0.0073051453, -0.03314209, -1.0728836E-4, 0.06021118, -0.029342651, -0.0026931763, -0.04171753, 0.017868042, 0.030975342, 0.02017212, -0.014427185, 0.06518555, 0.023742676, -0.040100098, 0.052612305, 0.0072746277, 0.026367188, 0.03060913, 0.0038013458, 5.054474E-4, 0.016647339, -0.02015686, 0.012512207, 0.04324341, 0.01436615, -0.026351929, -0.03060913, 0.011802673, -0.023666382, 0.01676941, -0.035125732, -0.005302429, 0.03024292, 0.01197052, 0.023086548, -0.036315918, -0.017120361, 0.034820557, -0.0061073303, -0.010307312, -0.04660034, 0.0140686035, -0.015823364, 0.030426025, 0.028778076, 8.8882446E-4, -0.030181885, 0.033843994, 0.0015392303, 0.02178955, 0.05569458, -0.035369873, 0.04776001, 0.033111572, 0.03805542, 0.053894043, -0.030166626, -0.0070762634, 0.038909912, 0.055145264, 0.090026855, 0.011062622, -0.012641907, -0.027374268, -0.0012702942, -0.09185791, 0.014801025, -0.024215698, 0.009162903, 0.020324707, -0.019317627, -0.016281128, -0.031463623, -0.006298065, 0.012260437, 0.012664795, 0.017700195, -0.019927979, 0.054138184, -0.049682617, 0.049743652, -0.0046920776, 0.031280518, -0.018249512, 0.00440979, 0.019683838, -0.014434814, 0.033203125, 0.007911682, 1.295805E-4, 0.0015935898, 0.022506714, -0.0011787415, 0.004852295, 0.046813965, -0.023986816, 0.055847168, -0.040771484, -0.010002136, 0.017990112, 0.034423828, 0.015350342, -0.0042800903, 2.2351742E-5, -0.02746582, 9.5939636E-4, 0.007003784, 4.9734116E-4, 0.023483276, -0.03375244, 0.047332764, -0.0013132095, 0.014976501, -0.05078125, 0.013542175, -0.0057258606, -0.028808594, -0.020401001, 0.031555176, -0.02684021, 0.044647217, 0.01676941, -0.028869629, 0.006614685, 0.017044067, -0.035949707, -0.016662598, 0.08081055, 0.0418396, -0.008079529, -0.053344727, 0.040985107, -0.020050049, -0.022460938, 0.03048706, -0.01965332, -0.007160187, -0.0010414124, 0.0056381226, 0.044311523, 0.024734497, -0.04019165, -0.005882263, -0.038116455, 0.044891357, -0.02


### Our dataset is now ready! Let's create our Self-Managed Vector Search Index.

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/llm-rag-self-managed-prep-3.png?raw=true" style="float: right; width: 600px; margin-left: 10px">

Our dataset is now ready. We chunked the documentation page into small sections, computed the embeddings and saved it as a Delta Lake table.

Next, we'll configure Databricks Vector Search to ingest data from this table.

Vector search index uses a Vector search endpoint to serve the embeddings (you can think about it as your Vector Search API endpoint). <br/>
Multiple Indexes can use the same endpoint. Let's start by creating one.

In [0]:
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient()

if VECTOR_SEARCH_ENDPOINT_NAME not in [e['name'] for e in vsc.list_endpoints()['endpoints']]:
  print(VECTOR_SEARCH_ENDPOINT_NAME)

print(VECTOR_SEARCH_ENDPOINT_NAME)

# VECTOR_SEARCH_ENDPOINT_NAME = 'vector-search-endpoint'

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
vector-search-endpoint


In [0]:
wait_for_vs_endpoint_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME)
print(f"Endpoint named {VECTOR_SEARCH_ENDPOINT_NAME} is ready.")

Endpoint named vector-search-endpoint is ready.



You can view your endpoint on the [Vector Search Endpoints UI](#/setting/clusters/vector-search). Click on the endpoint name to see all indexes that are served by the endpoint.

In [0]:
catalog = 'ling_test_demo'
db = 'default'

#The table we'd like to index
source_table_fullname = f"{catalog}.{db}.databricks_documentation"
# Where we want to store our index
vs_index_fullname = f"{catalog}.{db}.databricks_documentation_vs_index"

print(source_table_fullname)
print(vs_index_fullname)
print(VECTOR_SEARCH_ENDPOINT_NAME)

ling_test_demo.default.databricks_documentation
ling_test_demo.default.databricks_documentation_vs_index
vector-search-endpoint


In [0]:
from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c

#The table we'd like to index
source_table_fullname = f"{catalog}.{db}.databricks_documentation"
# Where we want to store our index
vs_index_fullname = f"{catalog}.{db}.databricks_documentation_vs_index"

if not index_exists(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname):
  print(f"Creating index {vs_index_fullname} on endpoint {VECTOR_SEARCH_ENDPOINT_NAME}...")
  vsc.create_delta_sync_index(
    endpoint_name=VECTOR_SEARCH_ENDPOINT_NAME,
    index_name=vs_index_fullname,
    source_table_name=source_table_fullname,
    pipeline_type='TRIGGERED',
    primary_key="id",
    embedding_dimension=1024, #Match your model embedding size (bge)
    embedding_vector_column="embedding"
  )

#Let's wait for the index to be ready and all our embeddings to be created and indexed
wait_for_index_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname)
print(f"index {vs_index_fullname} on table {source_table_fullname} is ready")

Creating index ling_test_demo.default.databricks_documentation_vs_index on endpoint vector-search-endpoint...
Waiting for index to be ready, this can take a few min... {'detailed_state': 'PROVISIONING_INDEX', 'message': 'Delta sync Index creation is pending. Check latest status in Delta Live Tables: https://dbc-57a6b8b4-32b6.cloud.databricks.com#joblist/pipelines/24c3db47-a4e0-41fb-a91a-d718f4ea8a20', 'indexed_row_count': 0, 'ready': False, 'index_url': 'dbc-57a6b8b4-32b6.cloud.databricks.com/api/2.0/vector-search/endpoints/vector-search-endpoint/indexes/ling_test_demo.default.databricks_documentation_vs_index'} - pipeline url:dbc-57a6b8b4-32b6.cloud.databricks.com/api/2.0/vector-search/endpoints/vector-search-endpoint/indexes/ling_test_demo.default.databricks_documentation_vs_index
Waiting for index to be ready, this can take a few min... {'detailed_state': 'PROVISIONING_PIPELINE_RESOURCES', 'message': 'Index is currently pending setup of pipeline resources. Check latest status in Del

## Searching for similar content

That's all we have to do. Databricks will automatically capture and synchronize new entries in your Delta Live Table.

Note that depending on your dataset size and model size, index creation can take a few seconds to start and index your embeddings.

Let's give it a try and search for similar content.

*Note: `similarity_search` also support a filters parameter. This is useful to add a security layer to your RAG system: you can filter out some sensitive content based on who is doing the call (for example filter on a specific department based on the user preference).*

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

question = "How can I track billing usage on my workspaces?"
response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": [question]})
embeddings = [e['embedding'] for e in response.data]

results = vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname).similarity_search(
  query_vector=embeddings[0],
  columns=["url", "content"],
  num_results=1)
docs = results.get('result', {}).get('data_array', [])
docs

[['https://docs.databricks.com/en/administration-guide/account-settings/usage-detail-tags.html',
  'Monitor usage using cluster, pool, and workspace tags  \nTo monitor cost and accurately attribute Databricks usage to your organization’s business units and teams (for chargebacks, for example), you can tag workspaces, clusters, and pools. These tags propagate both to detailed DBU usage reports and to AWS EC2 and AWS EBS instances for cost analysis.  \nTagged objects and resources',
  0.62081194]]

## Next step: Deploy our chatbot model with RAG

We've seen how Databricks Lakehouse AI makes it easy to ingest and prepare your documents, and deploy a Vector Search index on top of it with just a few lines of code and configuration.

This simplifies and accelerates your data projects so that you can focus on the next step: creating your real-time chatbot endpoint with well-crafted prompt augmentation.

Open the [02-Deploy-RAG-Chatbot-Model]($./02-Deploy-RAG-Chatbot-Model) notebook to create and deploy a chatbot endpoint.